# 1: インポート

# 2: データ読込み

# 3: 特徴量数値化

# 4: ハイパーパラメータの調整

# 5: 実装

# 6: 過学習の有無を確認

# 1: インポート

In [1]:
import pandas as pd
from pandas import Series,DataFrame

from sklearn import svm
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error

import numpy as np

import keras
from keras import regularizers
from keras.metrics import mae
from keras import regularizers
from keras.datasets import fashion_mnist
from keras.models import Sequential
from keras.layers import Dense, Dropout

import warnings
warnings.filterwarnings('ignore')

Using TensorFlow backend.


# 2: データの読み込み

In [2]:
data_set = pd.read_csv(rf'data.csv',sep=",", header=0)

x = DataFrame(data_set.drop(data_set[["Product", "Component", "target"]], axis=1))
y = DataFrame(data_set["target"])


tr_x ,va_x ,tr_y ,va_y = train_test_split(x,y,test_size=0.2, shuffle=False)

# 4: ハイパーパラメータの調整

In [21]:
from hyperopt import hp
from keras.callbacks import EarlyStopping
from keras.layers.advanced_activations import ReLU, PReLU
from keras.layers.core import Dense, Dropout
from keras.layers.normalization import BatchNormalization
from keras.models import Sequential
from keras.optimizers import Adagrad
from keras.optimizers import Adadelta
from keras.optimizers import Adam
from keras.optimizers import Adamax
from sklearn.preprocessing import StandardScaler

# 基本となるパラメータ
base_param = {
    'input_dropout': 0.0,
    'hidden_layers': 3,
    'hidden_units': 96,
    'hidden_activation': 'relu',
    'hidden_dropout': 0.2,
    'batch_norm': 'before_act',
    'optimizer': {'type': 'adam', 'lr': 0.001},
    'batch_size': 64,
}

# 探索するパラメータの空間を指定する
param_space = {
    'input_dropout': hp.quniform('input_dropout', 0, 0.1, 0.05),
    'hidden_layers': hp.quniform('hidden_layers', 2, 5, 1),
    'hidden_units': hp.quniform('hidden_units', 32, 256, 32),
    'hidden_activation': hp.choice('hidden_activation', ['prelu', 'relu']),
    'hidden_dropout': hp.quniform('hidden_dropout', 0, 0.3, 0.05),
    'batch_norm': hp.choice('batch_norm', ['before_act', 'no']),
    'optimizer': hp.choice('optimizer',
                           [{'type': 'adam',
                             'lr': hp.loguniform('adam_lr', np.log(0.00001), np.log(0.01))},
                            {'type': 'adagrad',
                             'lr': hp.loguniform('adagrad_lr', np.log(0.00001), np.log(0.01))},
                            {'type': 'adadelta',
                             'lr': hp.loguniform('adadelta_lr', np.log(0.00001), np.log(0.01))},
                            {'type': 'adamax',
                             'lr': hp.loguniform('adamax_lr', np.log(0.00001), np.log(0.01))}]),
    'batch_size': hp.quniform('batch_size', 32, 128, 32),
}

In [22]:
class MLP:

    def __init__(self, params):
        self.params = params
        self.scaler = None
        self.model = None

    def fit(self, tr_x, tr_y, va_x, va_y):

        # パラメータ
        input_dropout = self.params['input_dropout']
        hidden_layers = int(self.params['hidden_layers'])
        hidden_units = int(self.params['hidden_units'])
        hidden_activation = self.params['hidden_activation']
        hidden_dropout = self.params['hidden_dropout']
        batch_norm = self.params['batch_norm']
        optimizer_type = self.params['optimizer']['type']
        optimizer_lr = self.params['optimizer']['lr']
        batch_size = int(self.params['batch_size'])

        # 標準化
        self.scaler = StandardScaler()
        tr_x = self.scaler.fit_transform(tr_x)
        va_x = self.scaler.transform(va_x)

        self.model = Sequential()

        # 入力層
        self.model.add(Dropout(input_dropout, input_shape=(tr_x.shape[1],)))

        # 中間層
        for i in range(hidden_layers):
            self.model.add(Dense(hidden_units))
            if batch_norm == 'before_act':
                self.model.add(BatchNormalization())
            if hidden_activation == 'prelu':
                self.model.add(PReLU())
            elif hidden_activation == 'relu':
                self.model.add(ReLU())
            else:
                raise NotImplementedError
            self.model.add(Dropout(hidden_dropout))

        # 出力層
        self.model.add(Dense(1))

        # オプティマイザ
        if optimizer_type == 'adam':
            optimizer = Adam(lr=optimizer_lr, beta_1=0.9, beta_2=0.999, epsilon=1e-07, decay=0.)
        elif optimizer_type == 'adadelta':
            optimizer = Adadelta(lr=optimizer_lr, rho=0.95, epsilon=1e-07, decay=0.0)
        elif optimizer_type == 'adamax':
            optimizer = Adamax(lr=optimizer_lr, beta_1=0.9, beta_2=0.999, epsilon=1e-07, decay=0.0)
        elif optimizer_type == 'adagrad':
            optimizer = Adagrad(lr=optimizer_lr, epsilon=1e-07, decay=0.0)
        else:
            raise NotImplementedError
            

        # 目的関数、評価指標などの設定
        
        self.model.compile(loss='mean_absolute_error', optimizer=optimizer, metrics=['mae'])

        # エポック数、アーリーストッピング
        nb_epoch = 50
        patience = 20
        early_stopping = EarlyStopping(patience=patience, restore_best_weights=True)

        # 学習の実行
        history = self.model.fit(tr_x, tr_y,
                                 epochs=nb_epoch,
                                 batch_size=batch_size, verbose=1,
                                 validation_data=(va_x, va_y),
                                 callbacks=[early_stopping])

    def predict(self, x):
        # 予測
        x = self.scaler.transform(x)
        y_pred = self.model.predict(x)
        y_pred = y_pred.flatten()
        return y_pred



    
    

from hyperopt import fmin, tpe, STATUS_OK, Trials
from sklearn.metrics import log_loss
from sklearn.metrics import mean_absolute_error


def score(params):
    # パラメータセットを指定したときに最小化すべき関数を指定する
    # モデルのパラメータ探索においては、モデルにパラメータを指定して学習・予測させた場合のスコアとする
    model = MLP(params)
    model.fit(tr_x, tr_y, va_x, va_y)
    va_pred = model.predict(va_x)
    score = mean_absolute_error(va_y, va_pred)
    print(f'params: {params}, MAE: {score:.4f}')

    # 情報を記録しておく
    history.append((params, score))

    return {'loss': score, 'status': STATUS_OK}


# hyperoptによるパラメータ探索の実行
max_evals = 10
trials = Trials()
history = []
fmin(score, param_space, algo=tpe.suggest, trials=trials, max_evals=max_evals)


# 記録した情報からパラメータとスコアを出力する
# trialsからも情報が取得できるが、パラメータを取得しにくい
history = sorted(history, key=lambda tpl: tpl[1])
best = history[0]
print(f'best params:{best[0]}, score:{best[1]:.4f}')

Train on 15176 samples, validate on 3795 samples                                                                       
Epoch 1/50                                                                                                             
   64/15176 [..............................]                                                                           
 - ETA: 2:32 - loss: 0.0438 - mae: 0.0438                                                                              
                                                                                                                       
  448/15176 [..............................]                                                                           
 - ETA: 22s - loss: 0.0378 - mae: 0.0378                                                                               
                                                                                                                      
  512/15176 [>...........................

                                                                                                                       
 1856/15176 [==>...........................]                                                                           
 - ETA: 1s - loss: 0.0058 - mae: 0.0058                                                                                
                                                                                                                       
 2240/15176 [===>..........................]                                                                           
 - ETA: 1s - loss: 0.0058 - mae: 0.0058                                                                                
                                                                                                                       
 2624/15176 [====>.........................]                                                                           
 - ETA: 1s - loss: 0.0057 - mae: 0.0057 

 5056/15176 [========>.....................]                                                                           
 - ETA: 1s - loss: 0.0052 - mae: 0.0052                                                                                
                                                                                                                       
 5568/15176 [==========>...................]                                                                           
 - ETA: 1s - loss: 0.0052 - mae: 0.0052                                                                                
                                                                                                                       
 6016/15176 [==========>...................]                                                                           
 - ETA: 1s - loss: 0.0052 - mae: 0.0052                                                                                
                                        

 - ETA: 0s - loss: 0.0049 - mae: 0.0049                                                                                
                                                                                                                       
11904/15176 [======================>.......]                                                                           
 - ETA: 0s - loss: 0.0049 - mae: 0.0049                                                                                
                                                                                                                       
12416/15176 [=======================>......]                                                                           
 - ETA: 0s - loss: 0.0049 - mae: 0.0049                                                                                
                                                                                                                       
12928/15176 [========================>..

                                                                                                                       
 2048/15176 [===>..........................]                                                                           
 - ETA: 1s - loss: 0.0045 - mae: 0.0045                                                                                
                                                                                                                       
 2624/15176 [====>.........................]                                                                           
 - ETA: 1s - loss: 0.0045 - mae: 0.0045                                                                                
                                                                                                                       
 3136/15176 [=====>........................]                                                                           
 - ETA: 1s - loss: 0.0044 - mae: 0.0044 

...

 - ETA: 3s - loss: 0.1014 - mae: 0.1014                                                                                
                                                                                                                       
 1920/15176 [==>...........................]                                                                           
 - ETA: 3s - loss: 0.1021 - mae: 0.1021                                                                                
                                                                                                                       
 2176/15176 [===>..........................]                                                                           
 - ETA: 3s - loss: 0.0998 - mae: 0.0998                                                                                
                                                                                                                       
 2368/15176 [===>.......................

                                                                                                                       
12288/15176 [=======================>......]                                                                           
 - ETA: 0s - loss: 0.0993 - mae: 0.0993                                                                                
                                                                                                                       
12544/15176 [=======================>......]                                                                           
 - ETA: 0s - loss: 0.0992 - mae: 0.0992                                                                                
                                                                                                                       
12736/15176 [========================>.....]                                                                           
 - ETA: 0s - loss: 0.0991 - mae: 0.0991 

 6720/15176 [============>.................]                                                                           
 - ETA: 2s - loss: 0.1011 - mae: 0.1011                                                                                
                                                                                                                       
 6976/15176 [============>.................]                                                                           
 - ETA: 2s - loss: 0.1008 - mae: 0.1008                                                                                
                                                                                                                       
 7232/15176 [=============>................]                                                                           
 - ETA: 1s - loss: 0.1008 - mae: 0.1008                                                                                
                                        

 - ETA: 2s - loss: 0.0999 - mae: 0.0999                                                                                
                                                                                                                       
 2304/15176 [===>..........................]                                                                           
 - ETA: 2s - loss: 0.0983 - mae: 0.0983                                                                                
                                                                                                                       
 2496/15176 [===>..........................]                                                                           
 - ETA: 2s - loss: 0.0988 - mae: 0.0988                                                                                
                                                                                                                       
 2752/15176 [====>......................

                                                                                                                       
10880/15176 [====================>.........]                                                                           
 - ETA: 1s - loss: 0.1015 - mae: 0.1015                                                                                
                                                                                                                       
11136/15176 [=====================>........]                                                                           
 - ETA: 1s - loss: 0.1016 - mae: 0.1016                                                                                
                                                                                                                       
11328/15176 [=====================>........]                                                                           
 - ETA: 1s - loss: 0.1016 - mae: 0.1016 